In [1]:
import pandas as pd
import numpy as np

import pyodbc
import configparser


config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\Documents\Enviador de email\credenciais.ini")

conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

In [2]:
query = '''
select
	bvb.[DATA],
	bvb.pdv,
	bvb.SKU ,
	cast(replace(bvb.VENDAS,'.','') as int) as Vendas,
	em.ORIGEM
from base_vendas_bi bvb 
left join (
select *
from
estoque_mar
where origem is not null) em on cast(em.SKU as int) = cast(replace(bvb.SKU,'.','') as int) and cast( em.pdv as int) = cast(bvb.PDV as int)
WHERE EM.CATEGORIA not in ('SUPORTE À VENDA','EMBALAGENS') AND bvb.[DATA] >'2025-04-14'
'''
df_vendas = pd.read_sql(query, conn)
conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_16792\1235837546.py:16: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_vendas = pd.read_sql(query, conn)


In [3]:
df_vendas['pdv'] = np.where(df_vendas['pdv'] == '23703','23708',df_vendas['pdv'])

In [4]:
df_vendas['DATA'] = pd.to_datetime(df_vendas['DATA'])

df_vendas['DATA_MES'] = pd.to_datetime(df_vendas['DATA'], dayfirst=True, errors='coerce').dt.to_period('M').astype(str)

df_vendas['Vendas'] = df_vendas['Vendas'].astype('Int64')

In [5]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\Documents\compilado_tab_pedido.xlsx")

df_tabela['extracao_desc'] = df_tabela['Descrição'].str.split(' ').str[0]

In [6]:
df_tabela['LINHA'] = np.where(df_tabela['MARCA'] == 'EUDORA',df_tabela['extracao_desc'],df_tabela['LINHA'])

In [7]:
df_tabela = df_tabela.groupby(['Nome da Origem','SKU1', 'SKU2','Descrição', 'MARCA','CATEGORIA', 'LINHA','Tipo Preço','extracao_desc'])[['PC','PV']].max().reset_index()

In [8]:
df_vendas2 = pd.merge(df_vendas,df_tabela,left_on='SKU',right_on='SKU2',how='left')
df_vendas2 = df_vendas2.drop_duplicates()

In [9]:
df_vendas2['preço_venda'] = df_vendas2['Vendas']*df_vendas2['PV']

In [10]:
df_vendas2.shape

(1568926, 18)

In [11]:
df_vendas2['PV'] = df_vendas2['PV'].astype('str').str.replace(',','')
df_vendas2['PV'] = df_vendas2['PV'].astype('float')

In [12]:
df_vendas2['preço_venda'].sum()

np.float64(306748811.9699977)

In [13]:
df_vendas2[(df_vendas2['SKU']==84387)& (df_vendas2['pdv']=='20998')]['Vendas'].sum()

np.int64(16832)

In [14]:
# Agrupar vendas por PDV, Marca e SKU
vendas_por_pdv_sku = df_vendas2.groupby(['pdv', 'MARCA', 'SKU'])['preço_venda'].sum().reset_index()

# Ordenar por PDV, MARCA e vendas (maior para menor)
vendas_por_pdv_sku = vendas_por_pdv_sku.sort_values(['pdv', 'MARCA', 'preço_venda'], ascending=[True, True, False])

# Calcular percentual acumulado DENTRO de cada PDV e MARCA
vendas_por_pdv_sku['percentual_acumulado'] = vendas_por_pdv_sku.groupby(['pdv', 'MARCA'])['preço_venda'].transform(
    lambda x: (x.cumsum() / x.sum()) * 100
)

# Criar coluna CLASSE
vendas_por_pdv_sku['CLASSE'] = vendas_por_pdv_sku['percentual_acumulado'].apply(
    lambda x: 'A' if x <= 80 else ('B' if x <= 95 else 'C')
)


# Visualizar resultado
vendas_por_pdv2 =vendas_por_pdv_sku.reset_index().sort_values(['pdv','percentual_acumulado'])

In [15]:
vendas_por_pdv2 = vendas_por_pdv2.rename(columns={'pdv':'PDV'})

vendas_por_pdv2

index    PDV      MARCA    SKU  preço_venda  percentual_acumulado  \
0          972  12522  BOTICARIO  84387      31384.3              2.360871   
1          787  12522  BOTICARIO  75792      23384.4              4.119953   
2          747  12522  BOTICARIO  74043      22028.4               5.77703   
3          315  12522  BOTICARIO  50677      20946.9              7.352751   
4          816  12522  BOTICARIO  77524      19423.3              8.813861   
...        ...    ...        ...    ...          ...                   ...   
107809  107809   5699  BOTICARIO  87421          0.0                 100.0   
107810  107810   5699  BOTICARIO  87422          0.0                 100.0   
107811  107811   5699  BOTICARIO  87423          0.0                 100.0   
107812  107812   5699  BOTICARIO  87424          0.0                 100.0   
107813  107813   5699     EUDORA  53095          0.0                   NaN   

       CLASSE  
0           A  
1           A  
2           A  
3           A  
4           A  
...       ...  
107809      C  
107810      C  
107811      C  
107812      C  
107813      C  

[107814 rows x 7 columns]

In [16]:
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}")

query = '''
select
em.PDV,
em.SKU,
em.CLASSE as CLASSE_MAR
from estoque_mar em
'''
df_estoque = pd.read_sql(query, conn)
conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_16792\145927781.py:15: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_estoque = pd.read_sql(query, conn)


In [17]:
df_estoque['SKU'] = df_estoque['SKU'].astype('Int64')

In [18]:
vendas_por_pdv2 = vendas_por_pdv2.rename(columns={'pdv':'PDV'})

In [19]:
vendas_por_pdv3 = pd.merge(vendas_por_pdv2,df_estoque,on=['PDV','SKU'],how='left')

vendas_por_pdv3

index    PDV      MARCA    SKU  preço_venda  percentual_acumulado  \
0          972  12522  BOTICARIO  84387      31384.3              2.360871   
1          787  12522  BOTICARIO  75792      23384.4              4.119953   
2          747  12522  BOTICARIO  74043      22028.4               5.77703   
3          315  12522  BOTICARIO  50677      20946.9              7.352751   
4          816  12522  BOTICARIO  77524      19423.3              8.813861   
...        ...    ...        ...    ...          ...                   ...   
107809  107809   5699  BOTICARIO  87421          0.0                 100.0   
107810  107810   5699  BOTICARIO  87422          0.0                 100.0   
107811  107811   5699  BOTICARIO  87423          0.0                 100.0   
107812  107812   5699  BOTICARIO  87424          0.0                 100.0   
107813  107813   5699     EUDORA  53095          0.0                   NaN   

       CLASSE CLASSE_MAR  
0           A          A  
1           A          E  
2           A          A  
3           A          A  
4           A          A  
...       ...        ...  
107809      C          E  
107810      C          E  
107811      C          E  
107812      C          E  
107813      C          E  

[107814 rows x 8 columns]

In [20]:
vendas_por_pdv3.to_excel(r'C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\CODIGOS\Estudo Curva\avaliação_curva.xlsx',index=False)